# Migration and SLR Map using Plotly

In [2]:

%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import requests
import netCDF4
import plotly.graph_objects as go
import plotly.express as pex
from IPython.display import display

In [3]:
#initializing data
state_geo = requests.get(
    "https://raw.githubusercontent.com/python-visualization/folium-example-data/main/us_states.json"
).json() #json of coordinates of US States

#one year example data for migration percentage
state_data = {'AL': 0.47842242772262455, 'GA': 0.518683178127163, 'FL': 0.9847132248834792, 'TN': 0.8221331803556341, 'TX': 0.5577922044043915, 'MS': -0.12328830050337783, 'NC': 0.8335744219235106, 'CA': -0.936720841803338, 'VA': -0.06322114686168713, 'CO': 0.0955032101845048, 'LA': -0.701322304966245, 'SC': 1, 'OH': -0.090923050208341, 'NY': -1, 'MI': -0.07654284398380765, 'KY': 0.14881481414578585, 'IL': -0.9543932223778862, 'IN': 0.14591296921056446, 'WA': -0.07633749698667776, 'AZ': 1, 'PA': -0.1287044547172545, 'MO': 0.20278244616404434, 'MD': -0.34541661696001646, 'AR': 0.4838899966132396, 'OK': 0.5400217129006817, 'KS': -0.16411391915598555, 'NJ': -0.34641850316840267, 'NV': 0.8453867325766531, 'OR': -0.017239617796134206, 'WI': 0.00134852530825041, 'MA': -0.7546432218990559, 'HI': -0.6623184400167754, 'UT': 0.5034241016308523, 'AK': -0.6941196141969103, 'MN': -0.2854608633612983, 'NM': 0.06864135975878155, 'IA': -0.16718033953228367, 'WV': 0.056797015092467665, 'CT': -0.11152862028289504, 'NE': -0.1986535484485154, 'ID': 1, 'MT': 1, 'ME': 0.9913264864262062, 'WY': 0.41178471117950843, 'ND': -0.6553633928783055, 'NH': 0.8372084317590902, 'DE': 1, 'SD': 0.5006817721266825, 'RI': -0.019003609218291303, 'VT': 0.5094310173012042}

#converting the dict to a dataframe
data = {"States":list(state_data.keys()), "PercentageMigration":list(state_data.values())}
migration_df = pd.DataFrame.from_dict(data)
migration_df

States  PercentageMigration
0      AL             0.478422
1      GA             0.518683
2      FL             0.984713
3      TN             0.822133
4      TX             0.557792
5      MS            -0.123288
6      NC             0.833574
7      CA            -0.936721
8      VA            -0.063221
9      CO             0.095503
10     LA            -0.701322
11     SC             1.000000
12     OH            -0.090923
13     NY            -1.000000
14     MI            -0.076543
15     KY             0.148815
16     IL            -0.954393
17     IN             0.145913
18     WA            -0.076337
19     AZ             1.000000
20     PA            -0.128704
21     MO             0.202782
22     MD            -0.345417
23     AR             0.483890
24     OK             0.540022
25     KS            -0.164114
26     NJ            -0.346419
27     NV             0.845387
28     OR            -0.017240
29     WI             0.001349
30     MA            -0.754643
31     HI            -0.662318
32     UT             0.503424
33     AK            -0.694120
34     MN            -0.285461
35     NM             0.068641
36     IA            -0.167180
37     WV             0.056797
38     CT            -0.111529
39     NE            -0.198654
40     ID             1.000000
41     MT             1.000000
42     ME             0.991326
43     WY             0.411785
44     ND            -0.655363
45     NH             0.837208
46     DE             1.000000
47     SD             0.500682
48     RI            -0.019004
49     VT             0.509431

In [4]:
f = netCDF4.Dataset('c3s_obs-sl_glo_phy-ssh_my_twosat-l4-duacs-0.25deg_P1D_multi-vars_101.88W-49.12W_16.12N-51.88N_2021-01-01-2023-06-07.nc')

In [5]:
f.variables.keys()

dict_keys(['adt', 'err_sla', 'err_ugosa', 'err_vgosa', 'flag_ice', 'sla', 'tpa_correction', 'ugos', 'ugosa', 'vgos', 'vgosa', 'latitude', 'longitude', 'time'])

In [6]:
f.variables['adt'].dimensions

('time', 'latitude', 'longitude')

In [7]:
latitude_data = f.variables['latitude'][:]

In [8]:
def convert_numeric_time_to_datetime64(time, units, calendar):
    # Use netCDF4.num2date to convert numeric time values to datetime objects
    cftime_objs = netCDF4.num2date(time, units=units, calendar=calendar)
    
    # Convert cftime objects to numpy.datetime64 objects
    datetime64_objs = np.array([np.datetime64(date) for date in cftime_objs])
    
    return datetime64_objs

In [9]:
latitude = f.variables['latitude'][:]
longitude = f.variables['longitude'][:]
time = f.variables['time'][:]  # This is likely in a numeric format representing dates

# Convert numeric time to datetime
# This depends on the 'units' and 'calendar' attributes of the time variable
time_units = f.variables['time'].units
time_calendar = f.variables['time'].calendar if hasattr(f.variables['time'], 'calendar') else 'standard'
time_datetimes = netCDF4.num2date(time, units=time_units, calendar=time_calendar)
time_units = f.variables['time'].units
try:
    calendar = f.variables['time'].calendar
except AttributeError:  # In case the 'calendar' attribute is missing
    calendar = 'gregorian'  # or 'standard', choose a default


# Convert your numeric time values to numpy.datetime64 objects
converted_times = convert_numeric_time_to_datetime64(time, time_units, calendar)

# Since your dataset likely represents a 2D grid of points over multiple times, 
# we'll need to repeat the time array to match the number of latitude and longitude points
time_repeated = np.repeat(converted_times, latitude.size * longitude.size)

# Create a meshgrid for latitude and longitude, then flatten them for the DataFrame
lon, lat = np.meshgrid(longitude, latitude)
lon_flat = lon.flatten()
lat_flat = lat.flatten()

# Repeat latitude and longitude coordinates for each time step
lat_repeated = np.tile(lat_flat, len(time_datetimes))
lon_repeated = np.tile(lon_flat, len(time_datetimes))

# Now combine everything into a DataFrame
df = pd.DataFrame({
    'Time': time_repeated,
    'Latitude': lat_repeated,
    'Longitude': lon_repeated
})

/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/806924853.py:3: UserWarning: WARNING: valid_min not used since it
cannot be safely cast to variable data type
  time = f.variables['time'][:]  # This is likely in a numeric format representing dates
/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/806924853.py:3: UserWarning: WARNING: valid_max not used since it
cannot be safely cast to variable data type
  time = f.variables['time'][:]  # This is likely in a numeric format representing dates


In [10]:
display(df)

average_rows_per_day = latitude.size * longitude.size
average_rows_per_day

Time  Latitude  Longitude
0        2021-01-01    16.125   -101.875
1        2021-01-01    16.125   -101.625
2        2021-01-01    16.125   -101.375
3        2021-01-01    16.125   -101.125
4        2021-01-01    16.125   -100.875
...             ...       ...        ...
27108859 2023-06-07    51.875    -50.125
27108860 2023-06-07    51.875    -49.875
27108861 2023-06-07    51.875    -49.625
27108862 2023-06-07    51.875    -49.375
27108863 2023-06-07    51.875    -49.125

[27108864 rows x 3 columns]

30528

In [11]:
f.variables['time'][:].shape

/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/3621615317.py:1: UserWarning: WARNING: valid_min not used since it
cannot be safely cast to variable data type
  f.variables['time'][:].shape
/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/3621615317.py:1: UserWarning: WARNING: valid_max not used since it
cannot be safely cast to variable data type
  f.variables['time'][:].shape


(888,)

In [12]:
f.variables['latitude'][:].shape

(144,)

In [13]:
f.variables['longitude'][:].shape

(212,)

In [14]:
f.variables['time'][:].data.shape

/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/4216859518.py:1: UserWarning: WARNING: valid_min not used since it
cannot be safely cast to variable data type
  f.variables['time'][:].data.shape
/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/4216859518.py:1: UserWarning: WARNING: valid_max not used since it
cannot be safely cast to variable data type
  f.variables['time'][:].data.shape


(888,)

In [15]:
f.variables['adt'][:].data.max()

1.6931

In [16]:
vars = ['adt', 'err_sla', 'err_ugosa', 'err_vgosa', 'flag_ice', 'sla', 'tpa_correction', 'ugos', 'ugosa', 'vgos', 'vgosa']
for var_name in vars:
    # Assuming each variable has the same time, latitude, longitude dimensions
    # Here, we just showcase how you might access and reshape the data
    # In reality, you'll need to actually load the data from the NetCDF file similar to the latitude/longitude
    var_data = f.variables[var_name][:]  # This will need to be reshaped or repeated as necessary
    
    # Flatten or reshape the data to match the DataFrame structure
    # This step is crucial and will vary based on your specific data structure and needs
    var_data_flat = var_data.flatten().data  # Or another method to match DataFrame's structure
    try:
        # Add the data as a new column to the DataFrame
        df[var_name] = var_data_flat
    except Exception as e:
        print(f"Error adding {var_name} to DataFrame: {e}")

Error adding tpa_correction to DataFrame: Length of values (888) does not match length of index (27108864)


In [17]:
df['adt'].describe()

# Assuming df is your DataFrame and -2.147484e+09 is the placeholder value for land
sea_df = df[df['adt'] > -2.147484e+07]
sea_df['adt'].describe()

count    1.563753e+07
mean     5.168793e-01
std      3.445271e-01
min     -7.935000e-01
25%      2.958000e-01
50%      6.324000e-01
75%      7.612000e-01
max      1.693100e+00
Name: adt, dtype: float64

In [18]:
# Step 1: Reduce spatial resolution
nth_point = 10
reduced_df = sea_df.iloc[::nth_point, :]

# Step 2: Limit the time range (example: select the first 7 days)
unique_dates = reduced_df['Time'].unique()
selected_dates = unique_dates[:7]  # Adjust as needed
reduced_df = reduced_df[reduced_df['Time'].isin(selected_dates)]

# Plotting just the first date in the selected_dates for demonstration
first_date_df = reduced_df[reduced_df['Time'] == selected_dates[0]]

# Assuming 'df' is your DataFrame with columns for 'Time', 'Latitude', 'Longitude', and 'adt'
# First, ensure 'Time' is in datetime format and sort the DataFrame
sea_df['Time'] = pd.to_datetime(df['Time'])
sea_df.sort_values(by=['Latitude', 'Longitude', 'Time'], inplace=True)

# Group the data by 'Latitude' and 'Longitude' and calculate the difference in 'adt' values
# The 'diff()' function calculates the difference between consecutive rows within each group
sea_df['Rate_of_Change'] = sea_df.groupby(['Latitude', 'Longitude'])['adt'].diff()

# Optionally, fill NaN values that appear as a result of diff() for the first entry of each group with 0 or other appropriate value
sea_df['Rate_of_Change'].fillna(0, inplace=True)

/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/2585277536.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sea_df['Time'] = pd.to_datetime(df['Time'])
/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/2585277536.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sea_df.sort_values(by=['Latitude', 'Longitude', 'Time'], inplace=True)
/var/folders/0_/p6_60b2d3r33yjj108yb0_7r0000gn/T/ipykernel_66336/2585277536.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_in

In [19]:
# Get the start and end dates from the data
start_date = sea_df['Time'].min()
end_date = sea_df['Time'].max()

# Select data for a single day for simplicity in this example
single_day_df = sea_df[sea_df['Time'] == '2023-01-01']

# Calculate the average daily rate of change for each (Latitude, Longitude) over the available time range
# Group by 'Latitude' and 'Longitude' and then calculate the mean of 'Rate_of_Change'
avg_rate_of_change = sea_df.groupby(['Latitude', 'Longitude'])['Rate_of_Change'].mean().reset_index() 
avg_rate_of_change['Rate_of_Change'] *=  1000
# Scaling factor for visualization
size_scaling_factor = 10

# Create the figure
fig = go.Figure(data=go.Scattergeo(
    lon = avg_rate_of_change['Longitude'],
    lat = avg_rate_of_change['Latitude'],
    text = avg_rate_of_change['Rate_of_Change'].astype(str) + ' avg daily change',
    mode = 'markers',
    marker = dict(
        size = np.abs(avg_rate_of_change['Rate_of_Change']) * size_scaling_factor,  # Adjust size based on avg daily rate of change
        color = 'blue',  # Fixed color or adjust based on another variable
        colorscale = 'Viridis',
        showscale = True
    )
))

# Update map layout to focus on the specific area
fig.update_layout(
    title = f'Sea Surface Height (ADT) Average Daily Rate of Change: {start_date.strftime("%Y-%m-%d")} to {end_date.strftime("%Y-%m-%d")}',
    geo = dict(
        scope = 'north america',
        projection_type = "equirectangular",
        lataxis_range = [25, 45],  # Latitude range for the East Coast and Gulf of Mexico
        lonaxis_range = [-100, -65],  # Longitude range
    )
)

fig.show()

In [20]:
#plotly object that creates a choropleth map
fig = pex.choropleth(migration_df, geojson=state_geo, scope="usa", locations="States", color="PercentageMigration", color_continuous_scale="rdpu")

fig.show()

In [21]:
#function with all the previous parts together

#center coordinates of each state(not needed but kept just in case)
#coords = {'AL': [32.318230, -86.902298], 'GA': [33.247875, -83.441162], 'FL': [27.994402, -81.760254], 'TN': [35.860119, -86.660156], 'TX': [31.968599, -99.901813], 'MS': [32.354668, -89.398528], 'NC': [35.759573, -79.0193], 'CA': [36.778261, -119.417932], 'VA': [37.431573, -78.656894], 'CO': [39.550051, -105.782067], 'LA': [31.244823, -92.145024], 'SC': [33.836081, -81.163725], 'OH': [40.417287, -82.907123], 'NY': [43.299428, -74.217933], 'MI': [44.314844, -85.602364], 'KY': [37.839333, -84.270018], 'IL': [40.633125, -89.398528], 'IN': [40.551217, -85.602364], 'WA': [47.751074, -120.740139], 'AZ': [34.048928, -111.093731], 'PA': [41.203322, -77.194525], 'MO': [37.964253, -91.831833], 'MD': [39.045755, -76.641271], 'AR': [35.20105, -91.831833], 'OK': [35.007752, -97.092877], 'KS': [39.011902, -98.484246], 'NJ': [40.058324, -74.405661], 'NV': [38.80261, -116.419389], 'OR': [43.804133, -120.554201], 'WI': [43.78444, -88.787868], 'MA': [42.407211, -71.382437], 'HI': [19.898682, -155.665857], 'UT': [39.32098, -111.093731], 'AK': [63.588753, -154.493062], 'MN': [46.729553, -94.6859], 'NM': [34.97273, -105.032363], 'IA': [41.878003, -93.097702], 'WV': [38.597626, -80.454903], 'CT': [41.603221, -73.087749], 'NE': [41.492537, -99.901813], 'ID': [44.068202, -114.742041], 'MT': [46.879682, -110.362566], 'ME': [45.253783, -69.445469], 'WY': [43.075968, -107.290284], 'ND': [47.551493, -101.002012], 'NH': [43.193852, -71.572395], 'DE': [38.910832, -75.52767], 'SD': [43.969515, -99.901813], 'RI': [41.580095, -71.477429], 'VT': [44.558803, -72.577841]}
import plotly.express as px
import plotly.graph_objects as go
import numpy as np

state_geo = requests.get(
    "https://raw.githubusercontent.com/python-visualization/folium-example-data/main/us_states.json"
).json()

def migrationSLRMap(state_data: dict, avg_roc_lon: pd.DataFrame, avg_roc_lat: pd.DataFrame, year):
    data_migration = {"States":list(state_data.keys()), "PercentageMigration":list(state_data.values())}
    migration_df = pd.DataFrame.from_dict(data_migration)
    
    fig1 = pex.choropleth(migration_df, 
                          geojson=state_geo, 
                          locations="States", 
                          scope="usa",
                          color="PercentageMigration", 
                          color_continuous_scale="RdBu",
                          title=f'Visualize US Internal Migration Patterns Alongside Average Sea Level Increase: {year}', 
                          range_color = (-2,2)
                        )
    #updating choropleth color bar 
    fig1.update_layout(coloraxis_colorbar = dict(title="Change in Population (%)", orientation = "h", len=0.5))
    
    #SLR Scatterplot
    fig2 = go.Scattergeo(
        lon = avg_roc_lon,
        lat = avg_roc_lat,
        text = avg_rate_of_change['Rate_of_Change'].astype(str) + ' avg daily change',
        mode = 'markers',
        marker = dict(
            size = np.abs(avg_rate_of_change['Rate_of_Change']) * size_scaling_factor,  # Adjust size based on avg daily rate of change
            color = 'blue',  # Fixed color or adjust based on another variable
            colorscale = 'RdBu',
            showscale = False
        )
        
    )
    #adding the plots together
    fig1.add_trace(fig2)

    fig1.show()


In [24]:
import json
import netCDF4
import numpy as np
import pandas as pd
import plotly.express as pex
import plotly.graph_objects as go


# Load the JSON file
json_filename = "/Users/madelineshah/Documents/Clones/combined_migration_data.json"
with open(json_filename, 'r') as f:
    migration_data = json.load(f)

# Function to get migration data for a specific year
def get_migration_data(year):
    return migration_data.get(str(year), {})

# Example: Get migration data for the year 2012
year = 2018
state_data_year = get_migration_data(year)

# Now, call the migrationSLRMap function with the data for the specific year
migrationSLRMap(state_data_year, avg_rate_of_change['Longitude'], avg_rate_of_change['Latitude'], year)

In [23]:
print(avg_rate_of_change.head())


   Latitude  Longitude  Rate_of_Change
0    16.125   -101.875        0.226577
1    16.125   -101.625        0.198649
2    16.125   -101.375        0.176577
3    16.125   -101.125        0.166779
4    16.125   -100.875        0.164977
